![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS - B 2019 Visitas domiciliares de Equipe de Saúde da Família e Agentes de Endemias

## Bibliotecas Utilizadas

In [ ]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(tictoc)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [3]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2019>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2019>")

## Definição do peso e filtragem de respondentes do questionário

In [4]:
#Selecionando registros válidos e calculando peso amostral - summary de verificação
pns2019.1<-  <Coloque aqui o nome do arquivo RDATA>  %>% filter(V0025A==1) 
pns2019.1<- pns2019.1 %>% mutate(peso_moradores=((V00281*279382/209589607))) 
pns2019.1<-pns2019.1 %>% filter(!is.na(peso_moradores))
summary(pns2019.1$peso_moradores)

    Min.  1st Qu.   Median     Mean  3rd Qu.     Max. 
 0.01046  0.31515  0.58914  1.00000  1.16920 39.99838 

## Criação de variáveis dos indicadores

In [5]:
#Desfechos - Indicadores
# 1. Proporção de moradores em domicílios cadastrados em unidade de saúde da família - B001P.
pns2019.1 <- pns2019.1 %>% mutate(B001P=ifelse(B001==1, 1, 0))
pns2019.1$B001P <- factor(pns2019.1$B001P, levels=c(1, 0), labels=c("Sim", "Não"))
summary(pns2019.1$B001P)

Sim    Não 
183072  96310

In [6]:
# 2. Proporção de domicílios cadastrados em unidade de saúde da família há um ano ou mais e que recebem visita de Agente Comunitário em Saúde (ACS) ou membro da Equipe de Saúde da Família (ESF) mensalmente - B002P.
pns2019.1 <- pns2019.1 %>% mutate(B002P=ifelse(B002==4 & B003==1, 1, 0))
pns2019.1$B002P <- factor(pns2019.1$B002P, levels=c(1, 0), labels=c("Sim", "Não"))
summary(pns2019.1$B002P)

Sim    Não   NA's 
 66619 116453  96310

## Definições de abrangências

### Situação urbana ou rural

In [7]:
#Situação Urbano ou Rural
pns2019.1 <- pns2019.1 %>% rename(Sit_Urbano_Rural=V0026)
pns2019.1$Sit_Urbano_Rural<-factor(pns2019.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("urbano", "rural"))
summary(pns2019.1$Sit_Urbano_Rural)

urbano  rural 
212286  67096

### Sexo

In [8]:
#Sexo
pns2019.1 <- pns2019.1 %>% rename(Sexo=C006)
pns2019.1$Sexo<-factor(pns2019.1$Sexo, levels=c(1,2), labels=c("Masculino", "Feminino"))
summary(pns2019.1$Sexo)

Masculino  Feminino 
   134442    144940

### UF

In [9]:
#Estados - UFs
pns2019.1 <- pns2019.1 %>% rename(Unidades_da_Federacao=V0001)
pns2019.1$Unidades_da_Federacao<-factor(pns2019.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2019.1$Unidades_da_Federacao)

Rondônia                Acre            Amazonas             Roraima 
               7037                7808               12642                7995 
               Pará               Amapá           Tocantins            Maranhão 
              13475                6363                6127               17327 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               8745               14157                9472                9652 
         Pernambuco             Alagoas             Sergipe               Bahia 
              11934                9947                7803               10516 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
              14831               10078               13909               17522 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
              11237               10123                9878                8350 
        Mato Grosso               Goiás    Distrito Federal 
               7291                8003                7160

### Grandes Regiões

In [10]:
#Grandes Regiões
pns2019.1 <- pns2019.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2019.1$GrandesRegioes)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       61447        99553        56340        31238        30804

### Capital

In [11]:
#Capital
pns2019.1<- pns2019.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2019.1$Capital)

Porto Velho     Rio Branco         Manaus      Boa Vista          Belém 
          7037           7808          12642           7995          13475 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          6363           6127          17327           8745          14157 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          9472           9652          11934           9947           7803 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
         10516          14831          10078          13909          17522 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
         11237          10123           9878           8350           7291 
       Goiânia       Brasília 
          8003           7160

### Faixa Etária

In [12]:
#Faixas Etárias
pns2019.1 <-  pns2019.1 %>% mutate(faixa_idade=cut(C008,
  breaks = c(-Inf, 0.99, 4.99, 14.99, 24.99, 34.99, 44.99, 59.99, Inf),
  labels = c("Menor de 1 ano",
             "1 a 4 anos",
             "5 a 14 anos",
             "15 a 24 anos",
             "25 a 34 anos",
             "35 a 44 anos",
             "45 a 59 anos",
             "60 anos ou mais"), 
  ordered_result = TRUE, right = TRUE))
summary(pns2019.1$faixa_idade)

Menor de 1 ano      1 a 4 anos     5 a 14 anos    15 a 24 anos    25 a 34 anos 
           3349           14438           40500           43827           39854 
   35 a 44 anos    45 a 59 anos 60 anos ou mais 
          41460           52400           43554

### Raça

In [13]:
#Raça
pns2019.1 <- pns2019.1 %>% 
                mutate(Raca= ifelse(C009==1, 1, 
                             ifelse(C009==2, 2, 
                             ifelse(C009==4, 3, 9))))

pns2019.1$Raca<-factor(pns2019.1$Raca,
                       levels=c(1,2,3),
                       labels=c("Branca", "Preta", "Parda"))
summary(pns2019.1$Raca)

Branca  Preta  Parda   NA's 
 99019  28304 148273   3786

### Renda per capita

In [14]:
#Rendimento domiciliar per capita
pns2019.1 <- pns2019.1 %>% mutate(rend_per_capita = ifelse(VDF004 %in% 1:2, 1, 
                        ifelse(VDF004%in% 3, 2, 
                        ifelse(VDF004%in% 4, 3,
                        ifelse(VDF004%in% 5, 4, 
                        ifelse(is.na(VDF004)==TRUE, NA_real_, 5))))))

pns2019.1$rend_per_capita<-factor(pns2019.1$rend_per_capita,
                                  levels=c(1,2,3,4,5),
                                  labels=c("Até 1/2 SM",
                                           "1/2 até 1 SM",
                                           "1 até 2 SM",
                                           "2 até 3 SM",
                                           "Mais de 3 SM"))
summary(pns2019.1$rend_per_capita)

Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM         NA's 
       91898        81830        61643        19369        24470          172

### Escolaridade

In [15]:
# Escolaridade
pns2019.1 <- pns2019.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,
                        ifelse(is.na(VDD004A)==TRUE, NA_real_, 4)))))


pns2019.1$gescol<-factor(pns2019.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Fundamental incompleto ou equivalente",
                                           "Médio incompleto ou equivalente",
                                           "Superior incompleto ou equivalente",
                                           "Superior completo"))
summary(pns2019.1$gescol)

Fundamental incompleto ou equivalente       Médio incompleto ou equivalente 
                               121343                                 38564 
   Superior incompleto ou equivalente                     Superior completo 
                                71042                                 30646 
                                 NA's 
                                17787

## Criando indicadores

### Filtrando base de indicadores

In [16]:
#Selecionando variáveis para cálculo de indicadores no survey
pns2019Bsurvey<- pns2019.1 %>% select(
    "V0024","UPA_PNS","peso_moradores",
    "C008", "C009", "V0031", "VDF003", "B002",
    "Sit_Urbano_Rural", "Unidades_da_Federacao",
    "GrandesRegioes",  "Capital", "faixa_idade",
    "Raca", "rend_per_capita", "gescol", "Sexo",
    "B001P", "B002P") 


### Exporta tabela filtrada com os dados específicos - Módulo S 2019

In [17]:
#Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2019Ssurvey, file.path(diretorio_saida, "pns2019Ssurvey.csv"))

### Cria plano amostral complexo

In [18]:
desPNSB=svydesign(id=~UPA_PNS,
                  strat=~V0024,
                  weight=~peso_moradores,
                  nest=TRUE,
                  data=pns2019Bsurvey
                 )

In [19]:
desPNSB_C=subset(desPNSB,  !is.na(B001P) & V0031==1) 
desPNSB_R=subset(desPNSB,  !is.na(B001P) & !is.na(Raca))
desPNSB_RC=subset(desPNSB, !is.na(B001P) & !is.na(rend_per_capita)) 
desPNSB_GE=subset(desPNSB, !is.na(B001P) & !is.na(gescol))

In [20]:
desPNSB002P=subset(desPNSB, !is.na(B002P) & B002==4)
desPNSB002P_C=subset(desPNSB002P,  V0031==1)
desPNSB002P_R=subset(desPNSB002P,  !is.na(Raca)) 
desPNSB002P_RC=subset(desPNSB002P, !is.na(rend_per_capita)) 
desPNSB002P_GE=subset(desPNSB002P, !is.na(gescol))

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [21]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [22]:
ListaIndicadores = c(~B001P, ~B002P)
ListaIndicadoresTexto = c("B001P", "B002P")
ListaTotais = c('Brasil','Capital')
Ano <- "2019"

In [23]:
ListaDominios = c(~Raca,~rend_per_capita,~faixa_idade,~Sit_Urbano_Rural,
                  ~Sexo, ~Unidades_da_Federacao,~GrandesRegioes,~Capital,~gescol)
ListaDominiosTexto = c("raça","rend_per_capita","faixa_idade","urb_rur",
                       "Sexo", "uf","região","capital","gescol") 

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [24]:
#Cálculo dos indicadores usando o pacote survey 
i <- 0
#Para cada indicador
for(indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
    #Para cada dominio
    for (dominio in ListaDominios){
               #design especifico para capital que é subconjunto do dataframe total
               if (ListaDominiosTexto[j]=="capital"){
                   #designs especificos por variavel que são subconjuntos do dataset total
                   if(ListaIndicadoresTexto[i] == "B001P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSB_C, svymean,vartype= c("ci", "cv"))
                   }
                   else{
                     dataframe_indicador<-svyby(indicador, dominio, desPNSB002P_C, svymean,vartype= c("ci", "cv"))
                   }
               #Uso design do subconjunto para raça/cor que inclui preta,branca e parda as outras 
               # conjunto com nulos
               }else if (ListaDominiosTexto[j]=="raça"){
                   if(ListaIndicadoresTexto[i] == "B001P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSB_R, svymean,vartype= c("ci", "cv"))
                   }
                   else{
                       dataframe_indicador<-svyby(indicador, dominio, desPNSB002P_R, svymean,vartype= c("ci", "cv"))
                   }
               #design geral para o subconjunto de renda
               # conjunto com nulos
               } else if (ListaDominiosTexto[j]=="rend_per_capita"){
                   if(ListaIndicadoresTexto[i] == "B001P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSB_RC, svymean,vartype= c("ci", "cv"))
                   }
                   else{
                       dataframe_indicador<-svyby( indicador, dominio, desPNSB002P_RC, svymean,vartype= c("ci", "cv"))
                       }     
               #design geral para o subconjunto de escolaridade
               # conjunto com nulos
               } else if (ListaDominiosTexto[j]=="gescol"){
                   if(ListaIndicadoresTexto[i] == "B001P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSB_GE, svymean,vartype= c("ci", "cv"))
                   }
                   else{
                       dataframe_indicador<-svyby(indicador, dominio, desPNSB002P_GE, svymean,vartype= c("ci", "cv"))
                       }

               } else if(ListaIndicadoresTexto[i] == "B001P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSB, svymean,vartype= c("ci", "cv"))
                   }
                   else{
                     dataframe_indicador<-svyby(indicador, dominio, desPNSB002P, svymean,vartype= c("ci", "cv"))
                   }
               #União do dataframe de indicadores no formato do painel disponibilizado para PNS
               dataframe_indicador<-data.frame(dataframe_indicador)
               
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
    }
}

#### Criando a tabela pela abrangência total

In [25]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [26]:
i=0
#para cada indicador
for(indicador in ListaIndicadores){
    i <- i+1
    #para os totais Brasil e total das capitais
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        #Uso do design que é subconjunto do dataset para cada Capital
        if (total == "Capital"){
                   #Indicadores que são subconjunto do dataset tot
                   if(ListaIndicadoresTexto[i] == "B001P"){
                           dataframe_indicador <- svymean(indicador, desPNSB_C)
                   }
                   else {
                       dataframe_indicador <- svymean(indicador, desPNSB002P_C)
                   }
                   
        } else {
                   if(ListaIndicadoresTexto[i] == "B001P"){
                           dataframe_indicador <- svymean(indicador, desPNSB)
                   }
                   else {
                       dataframe_indicador <- svymean(indicador, desPNSB002P)
                   }
                       
        }

      
       intervalo_confianca <- confint(dataframe_indicador)
       coeficiente_variacao <- cv(dataframe_indicador)
       dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
       dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))

       dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        
       dataframe_indicador <- dataframe_indicador %>% 
                                 slice(1)
       colnames(dataframe_indicador) <- c('Sim','LowerS','UpperS','cvS')
       dataframe_indicador <- dataframe_indicador %>% 
                               select('Sim','LowerS','UpperS','cvS')
       dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
       dataframe_indicador$abr_tipo <- "total"
       dataframe_indicador$abr_nome <- total
       dataframe_indicador$Ano <- Ano 
       dataframe_indicador <- dataframe_indicador %>% 
                            select("abr_tipo","abr_nome","Ano","Indicador",'Sim','LowerS','UpperS','cvS')
       
       matriz_totais <-rbind(matriz_totais,dataframe_indicador)
        
    }
}

In [27]:
matriz_totais

abr_tipo abr_nome Ano  Indicador Sim       LowerS    UpperS   
B001PSim  total    Brasil   2019 B001P     0.6259929 0.6151817 0.6368042
B001PSim1 total    Capital  2019 B001P     0.4831397 0.4669895 0.4992899
B002PSim  total    Brasil   2019 B002P     0.3874185 0.3770887 0.3977482
B002PSim1 total    Capital  2019 B002P     0.2115345 0.1931174 0.2299517
          cvS        
B001PSim  0.008811672
B001PSim1 0.017055193
B002PSim  0.013603823
B002PSim1 0.044421477

#### Unindo tabela de indicadores e de totais

In [28]:
matrizIndicadores<-rbind(matrizIndicadores, matriz_totais)

#### Visualizando tabela de indicadores

In [30]:
matrizIndicadores[matrizIndicadores$abr_tipo=='rend_per_capita' &
                  matrizIndicadores$Indicador=='B002P', ]

abr_tipo        abr_nome     Ano  Indicador Sim       LowerS   
Até 1/2 SM1   rend_per_capita Até 1/2 SM   2019 B002P     0.4440943 0.4274397
1/2 até 1 SM1 rend_per_capita 1/2 até 1 SM 2019 B002P     0.3970010 0.3825221
1 até 2 SM1   rend_per_capita 1 até 2 SM   2019 B002P     0.3587589 0.3422701
2 até 3 SM1   rend_per_capita 2 até 3 SM   2019 B002P     0.3086167 0.2814417
Mais de 3 SM1 rend_per_capita Mais de 3 SM 2019 B002P     0.2273049 0.2004714
              UpperS    cvS       
Até 1/2 SM1   0.4607488 0.01913418
1/2 até 1 SM1 0.4114800 0.01860795
1 até 2 SM1   0.3752476 0.02344967
2 até 3 SM1   0.3357918 0.04492655
Mais de 3 SM1 0.2541385 0.06023125

#### Exportando tabela de indicadores calculados - Módulo S 2019

In [31]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores, file=paste0(diretorio_saida, "Indicadores_2019B_R.csv"), sep = ";", dec = ",", row.names = FALSE)